## Colab-Import

In [1]:
!pip install sentence_transformers
!apt install libomp-dev
!pip install faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 2.4 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-m

In [2]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 5.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 MB 13.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.6 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.31.0
    Uninstalling requests-2.31.0:
      Successfully uninstalled requests-2.31.0
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 2

In [3]:
from google.colab import drive
import numpy as np
import os
import glob
import nltk
import re
import string
import numpy as np
from sentence_transformers import SentenceTransformer, util
import faiss
from nltk.corpus import stopwords, wordnet
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.text import Text


nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [4]:
drive.mount('/content/drive')


Mounted at /content/drive


In [5]:
os.chdir('/content/drive/MyDrive/Colab Notebooks')


--------------

## Dateien einlesen und säubern

In [6]:
#hitler_path = "/home/simon/Dokumente/Uni Würzburg/Digital Humanities/Bachelorarbeit/datasets/MeinK/stalag_edition/CUT_Mein Kampf Stalag Edition _djvu.txt" #linux path

hitler_path = 'datasets/MeinK/stalag_edition/CUT_Mein Kampf Stalag Edition _djvu.txt' #colab path

#colab-absturz, daher jetzt besser einzeln untersucht
#hitler_path = 'datasets/MeinK/stalag_edition/buch01_kapitel/chapter01_buch01.txt' #colab path

In [7]:
#trump_path = "/home/simon/Dokumente/Uni Würzburg/Digital Humanities/Bachelorarbeit/datasets/my_trump/00_cleaned_files/all_files.txt" #linux path

trump_path = "datasets/my_trump/00_cleaned_files/all_files.txt" #colab path

#nur 2024
#trump_path = 'datasets/my_trump/00_cleaned_files/all_files_2024' #colab path

In [8]:
biden_path = "datasets/my_biden/00_cleaned_files/all_files.txt"

In [9]:
bush_path = "datasets/my_bush/all_files.txt"

In [82]:
obama_path = "datasets/my_obama/all_files.txt"

In [ ]:
"""#EINLESEN VON NUR BESTIMMTEN ORDNERN
def read_text_files_from_folders(folders):
    all_texts = []  #liste zum speichern der inhalte aller textdateien
    for folder in folders:
        #suche nach allen textdateien im aktuellen ordner
        for file_path in glob.glob(os.path.join(folder, '*.txt')):
            with open(file_path, 'r', encoding='utf-8') as file:
                all_texts.append(file.read())
    return all_texts  #gibt liste mit allen textdateien zurück

#ordnerlist aus denen textdateien eingelesen werden sollen
folders = ["datasets/my_biden/00_cleaned_files/2024", "datasets/my_biden/00_cleaned_files/2023", "datasets/my_biden/00_cleaned_files/2022"]

#beispiel biden
biden = read_text_files_from_folders(folders)
biden = "".join(biden)
print(biden)"""

'#EINLESEN VON NUR BESTIMMTEN ORDNERN\ndef read_text_files_from_folders(folders):\n    all_texts = []  #liste zum speichern der inhalte aller textdateien\n    for folder in folders:\n        #suche nach allen textdateien im aktuellen ordner\n        for file_path in glob.glob(os.path.join(folder, \'*.txt\')):\n            with open(file_path, \'r\', encoding=\'utf-8\') as file:\n                all_texts.append(file.read())\n    return all_texts  #gibt liste mit allen textdateien zurück\n\n#ordnerlist aus denen textdateien eingelesen werden sollen\nfolders = ["datasets/my_biden/00_cleaned_files/2024", "datasets/my_biden/00_cleaned_files/2023", "datasets/my_biden/00_cleaned_files/2022"]\n\n#beispiel biden\nbiden = read_text_files_from_folders(folders)\nbiden = "".join(biden)\nprint(biden)'

In [11]:
with open(hitler_path, 'r') as f:
    hitler = f.read()
    hitler = hitler.replace("\n", "")
hitler = re.sub(r'\d', '', hitler)
print(hitler[:1000])

AUTHOR’S PREFACE On April Ist, , I began to serve my sentence of detention in the Fortress of Landsberg am Lech, following the verdict pronounced by the Munich People’s Court on that day. After years of uninterrupted labour it was now possible for the first time to begin a work for which many had asked and which I myself felt would be profitable for the Movement. I therefore decided to devote two volumes to a description not only of the aims of our Movement, but also of its development. There is more to be learned from this than from any purely doctrinaire treatise. This has also given me the opportunity of describing my own development in so far as such a description s necessary to the understanding of the first as well as of the second volume and to refute the unfounded tales which the Jewish press has circulated about me. In this work I turn not to strangers, but to those followers of the Movement whose hearts belong to it and who wish to study it more profoundly. I know that fewer 

In [12]:
with open(trump_path, 'r') as f:
    trump = f.read()
print(trump[:100])

Thank you very much. Thank you.

Good evening. I’d like to provide the American people with an updat


In [13]:
with open(biden_path, 'r') as f:
  biden = f.read()
print(biden[:100])

 And thanks for joining me. I’m here, the FEMA Director is on, FEMA Director Chris Welsh. She’s on. 


In [14]:
with open(bush_path, 'r') as f:
  bush = f.read()
print(bush[:100])

From the East Room of the White House, President Bush clarifies his "balanced approach" to stem cell


In [84]:
with open(obama_path, 'r') as f:
  obama = f.read()
print(obama[:100])

President Obama delivers an address to the nation on immigration.
My fellow Americans, tonight, I’d 


In [16]:
def tok_sents(text):

    sentences = sent_tokenize(text)
    sents = [sentence for sentence in sentences]
    return sents

In [17]:
hitler = tok_sents(hitler)
#hitler = hitler[:10]
print(hitler)
print(f'Anzahl der Sätze: {len(hitler)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in hitler)}')

['AUTHOR’S PREFACE On April Ist, , I began to serve my sentence of detention in the Fortress of Landsberg am Lech, following the verdict pronounced by the Munich People’s Court on that day.', 'After years of uninterrupted labour it was now possible for the first time to begin a work for which many had asked and which I myself felt would be profitable for the Movement.', 'I therefore decided to devote two volumes to a description not only of the aims of our Movement, but also of its development.', 'There is more to be learned from this than from any purely doctrinaire treatise.', 'This has also given me the opportunity of describing my own development in so far as such a description s necessary to the understanding of the first as well as of the second volume and to refute the unfounded tales which the Jewish press has circulated about me.', 'In this work I turn not to strangers, but to those followers of the Movement whose hearts belong to it and who wish to study it more profoundly.',

In [18]:
trump = tok_sents(trump)
#trump = trump[:10]
print(trump)
print(f'Anzahl der Sätze: {len(trump)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in trump)}')

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Anzahl der Wörter: 857323


In [19]:
biden = tok_sents(biden)
#biden = biden[:10]
print(biden)
print(f'Anzahl der Sätze: {len(biden)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in biden)}')

[' And thanks for joining me.', 'I’m here, the FEMA Director is on, FEMA Director Chris Welsh.', 'She’s on.', 'And I’m here with my Senior Advisor and a boy who knows Louisiana, very, very well, man, and New Orleans and .', 'And what I’m going to do is make a brief statement here and then go through and tell you what we’re doing, but then hear from all of you, if that’s okay.', 'I know you’re busy as the devil.', 'I know you’ve got a lot to manage in your states, but the fact is that I want to hear from you.', 'We both want to hear from you.', 'And we know Hurricane Ida had a potential to cause massive, massive damage, and that’s exactly what we saw.', 'We already know there’s been at least one confirmed death and that number is likely to grow.', 'We’ve got a million people in Louisiana without power and for a time Ida caused the Mississippi River to literally change its direction.', 'And some folks are still dealing with the storm surge and flash flooding.', 'And there are roads that 

In [20]:
bush = tok_sents(bush)
#biden = biden[:10]
print(bush)
print(f'Anzahl der Sätze: {len(bush)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in bush)}')

['From the East Room of the White House, President Bush clarifies his "balanced approach" to stem cell research, in the context of two bills on the subject passed by Congress.', 'Good afternoon.', 'Congress has just passed and sent to my desk two bills concerning the use of stem cells in biomedical research.', 'These bills illustrate both the promise and perils we face in the age of biotechnology.', 'In this new era, our challenge is to harness the power of science to ease human suffering without sanctioning the practices that violate the dignity of human life.', 'In 2001, I spoke to the American people and set forth a new policy on stem cell research that struck a balance between the needs of science and the demands of conscience.', 'When I took office, there was no federal funding for human embryonic stem cell research.', 'Under the policy I announced five years ago, my administration became the first to make federal funds available for this research, yet only on embryonic stem cell 

In [85]:
obama = tok_sents(obama)
#biden = biden[:10]
print(obama)
print(f'Anzahl der Sätze: {len(obama)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in obama)}')

['President Obama delivers an address to the nation on immigration.', 'My fellow Americans, tonight, I’d like to talk with you about immigration.', 'For more than 200 years, our tradition of welcoming immigrants from around the world has given us a tremendous advantage over other nations.', 'It’s kept us youthful, dynamic, and entrepreneurial.', 'It has shaped our character as a people with limitless possibilities –- people not trapped by our past, but able to remake ourselves as we choose.', 'But today, our immigration system is broken -- and everybody knows it.', 'Families who enter our country the right way and play by the rules watch others flout the rules.', 'Business owners who offer their workers good wages and benefits see the competition exploit undocumented immigrants by paying them far less.', 'All of us take offense to anyone who reaps the rewards of living in America without taking on the responsibilities of living in America.', 'And undocumented immigrants who desperately

In [ ]:
"""#IGNORIEREN WENN SÄTZE UNGEFILTERT ANALYSIERT WERDEN

def get_wordnet_pos(word):
    """Maps POS tag to the WordNet POS tag."""
    tag = nltk.pos_tag([word])[0][1][0].upper()
    tag_dict = {
        'J': wordnet.ADJ,
        'N': wordnet.NOUN,
        'V': wordnet.VERB,
        'R': wordnet.ADV
    }
    return tag_dict.get(tag, wordnet.NOUN)

def preprocess_text(sentences, language='english'):
    stop_words = set(stopwords.words(language))
    lemmatizer = WordNetLemmatizer()
    filtered_sentences = []

    #sonderzeichen, die normal nicht in string.punctuation enthalten sind filtern lassen
    special_chars = set("“”‘’´`'\"")

    for sentence in sentences:
        #entferne sonderzeichen
        sentence = ''.join([char for char in sentence if char not in special_chars])

        words = word_tokenize(sentence)
        filtered_words = [
            lemmatizer.lemmatize(word.lower(), get_wordnet_pos(word))
            for word in words
            if word.lower() not in stop_words and not word.isdigit() and not word in string.punctuation
        ]
        filtered_sentence = ' '.join(filtered_words)
        filtered_sentences.append(filtered_sentence)

    return filtered_sentences

#eingelesene texte
hitler = preprocess_text(hitler)
trump = preprocess_text(trump)

print(hitler[:10])
print(trump[:10])
"""

KeyboardInterrupt: 

In [22]:
print('Hitler:')
print(f'Anzahl der Sätze: {len(hitler)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in hitler)}')
print('*'*50)
print('Trump:')
print(f'Anzahl der Sätze: {len(trump)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in trump)}')
print('*'*50)
print('Biden:')
print(f'Anzahl der Sätze: {len(biden)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in biden)}')
print('*'*50)
print('Bush:')
print(f'Anzahl der Sätze: {len(bush)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in bush)}')
print('*'*50)
print('Obama:')
print(f'Anzahl der Sätze: {len(obama)}')
print(f'Anzahl der Wörter: {sum(len(word_tokenize(sentence)) for sentence in obama)}')

Hitler:
Anzahl der Sätze: 9050
Anzahl der Wörter: 286456
**************************************************
Trump:
Anzahl der Sätze: 59761
Anzahl der Wörter: 857323
**************************************************
Biden:
Anzahl der Sätze: 13966
Anzahl der Wörter: 273543
**************************************************
Bush:
Anzahl der Sätze: 5989
Anzahl der Wörter: 122373
**************************************************
Obama:
Anzahl der Sätze: 10838
Anzahl der Wörter: 239990


----------------

## Kosinus-Ähnlichkeit berechnen (für alle Wörter)

In [ ]:
#ALT (nur vergleich hitler-trump)
#durchlaufzeit in colab: ca. 8 minuten


#festgelegtes modell
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')

#eingelesene texte und namensausgabe
text1 = hitler
text2 = biden

name1 = input().title() #name aus text1 eingeben
name2 = input().title() #name aus text2 eingeben


#embeddings berechnen
embeddings1 = model.encode(text1, convert_to_tensor=True)
embeddings2 = model.encode(text2, convert_to_tensor=True)

#faiss-integration
index = faiss.IndexFlatL2(embeddings2.shape[1])  #verwendet l2-distanz (euklidisch)
faiss.normalize_L2(embeddings2.numpy())
index.add(embeddings2.numpy())

#suche für jedes embedding aus text 1 die nächsten nachbarn in Text 2
k = 10  # anzahl der nächsten nachbarn
distances, indices = index.search(embeddings1.numpy(), k)

#funktion zur Berechnung der Manhattan-Distanz
def manhattan_distance(vec1, vec2):
    return np.sum(np.abs(vec1 - vec2))

#funktion zur Berechnung der Minkowski-Distanz
def minkowski_distance(vec1, vec2, p=3):
    return np.sum(np.abs(vec1 - vec2) ** p) ** (1 / p)

#filtert sätze nach threshold
similar_pairs = []
similarity_threshold = 0.3  #threshold-wert für cosine similarity
p_value = 3  #beispiel für den Parameter p der Minkowski-Distanz

for i, (dists, inds) in enumerate(zip(distances, indices)):
    for dist, idx in zip(dists, inds):
        sentence1 = text1[i]
        sentence2 = text2[idx]
        if len(sentence1.split()) >= 4 and len(sentence2.split()) >= 4:
            cosine_sim = util.pytorch_cos_sim(embeddings1[i].unsqueeze(0), embeddings2[idx].unsqueeze(0)).item()
            if cosine_sim > similarity_threshold:
                manhattan_dist = manhattan_distance(embeddings1[i].numpy(), embeddings2[idx].numpy())
                minkowski_dist = minkowski_distance(embeddings1[i].numpy(), embeddings2[idx].numpy(), p=p_value)
                similar_pairs.append((sentence1, sentence2, f"{name1} - Satz{i+1}", f"{name2} - Satz{idx+1}", dist, cosine_sim, manhattan_dist, minkowski_dist))

#ausgabe sortiert nach höchster cosine similarity (über reverse=True)
similar_pairs.sort(key=lambda x: x[5], reverse=True)

#ausgabe nach cosine sim und euklidischer distanz
print("Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):")
for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
    print(f"{source1}: \"{sentence1}\" \n{source2}: \"{sentence2}\"")
    print(f"***Cosine-Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n")


#ausgabe der ähnlichen paare in eine textdatei schreiben
input_name = input("Bitte Biden/Trump/Hitler/Bush eingeben...").lower()
output_file = "similar_pairs" + "_" + input_name + ".txt"
with open(output_file, "w", encoding="utf-8") as file:
    file.write("Gefilterte Sätze mit Cosine Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine Similarity sortiert):\n\n")
    for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
        file.write(f"{source1}: \"{sentence1}\"\n{source2}: \"{sentence2}\"\n")
        file.write(f"***Cosine Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n\n")

print(f"Die ähnlichen Sätze wurden in die Datei '{output_file}' geschrieben.")

Output hidden; open in https://colab.research.google.com to view.

----------------------

## Stichwörter nach Sätzen untersuchen (Konkordanz)

In [23]:
#funktion zum zerlegen von sätzen in wörter
def split_sentences(sentences):
  words = []
  for sentence in sentences:
    #trenne wörter durch leerzeichen
    words.extend(re.split(r'\s+', sentence))
  return words

In [24]:
#konvertieren von sätzen in wörter
word_list_hitler = split_sentences(hitler)

#drucken der liste der wörter
print(word_list_hitler[:20])

['AUTHOR’S', 'PREFACE', 'On', 'April', 'Ist,', ',', 'I', 'began', 'to', 'serve', 'my', 'sentence', 'of', 'detention', 'in', 'the', 'Fortress', 'of', 'Landsberg', 'am']


In [25]:
#konvertieren von sätzen in wörter
word_list_trump = split_sentences(trump)

#drucken der liste der wörter
print(word_list_trump[:20])

['Thank', 'you', 'very', 'much.', 'Thank', 'you.', 'Good', 'evening.', 'I’d', 'like', 'to', 'provide', 'the', 'American', 'people', 'with', 'an', 'update', 'on', 'our']


In [26]:
#konvertieren von sätzen in wörter
word_list_biden = split_sentences(biden)

#drucken der liste der wörter
print(word_list_biden[:20])

['', 'And', 'thanks', 'for', 'joining', 'me.', 'I’m', 'here,', 'the', 'FEMA', 'Director', 'is', 'on,', 'FEMA', 'Director', 'Chris', 'Welsh.', 'She’s', 'on.', 'And']


In [27]:
#konvertieren von sätzen in wörter
word_list_bush = split_sentences(bush)

#drucken der liste der wörter
print(word_list_bush[:20])

['From', 'the', 'East', 'Room', 'of', 'the', 'White', 'House,', 'President', 'Bush', 'clarifies', 'his', '"balanced', 'approach"', 'to', 'stem', 'cell', 'research,', 'in', 'the']


In [28]:
#konvertieren von sätzen in wörter
word_list_obama = split_sentences(obama)

#drucken der liste der wörter
print(word_list_obama[:20])

['President', 'Obama', 'delivers', 'an', 'address', 'to', 'the', 'nation', 'on', 'immigration.', 'My', 'fellow', 'Americans,', 'tonight,', 'I’d', 'like', 'to', 'talk', 'with', 'you']


-----------------------------

#### Funktion zur Extraktion von Sätzen mit dem Suchwort

In [29]:
#funktion zur extraktion von sätzen über suchwort
def extract_sentences_with_word(text, input_word):

    #lowercase umwandlung
    text = [sentence.lower() for sentence in text]

    #sätze nach suchwort filtern
    sentences_with_word = {sentence.strip() for sentence in text if input_word in sentence}

    return sentences_with_word

#### Analyse-Wort

In [47]:
input_word = input("Bitte ein Wort zur Analyse eingeben...").lower()

Bitte ein Wort zur Analyse eingeben...power


#### Hitler

In [48]:
#kurze übersicht über konkordanzen
text_hitler = Text(word_list_hitler)

textList_mk = Text(text_hitler)
textList_mk.concordance(input_word, width=100, lines=5)
textList_mk = textList_mk.concordance_list(input_word, width=22, lines=1000)
textList_mk = [' '.join(line.left) + ' ' + input_word + ' ' + ' '.join(line.right) for line in textList_mk]
textList_mk[:10]

Displaying 5 of 165 matches:
er. Imprecations and threats had no longer any power to change it. I wanted to become a painter and
change it. I wanted to become a painter and no power on earth could force me to become a civil serv
 came to know my fellow workmen better, and no power in the world could have moved me to join an or
ed a diabolical plane to weaken their fighting power and, if possible, to paralyse it. In view of t
ese new States were able to exercise a greater power of attraction than the German element. Even Vi


['threats had no longer any power to change it. I',
 'become a painter and no power on earth could force',
 'fellow workmen better, and no power in the world could',
 'plane to weaken their fighting power and, if possible, to',
 'able to exercise a greater power of attraction than the',
 'State even though the ruling power be grossly inefficient. When',
 'have resulted in leaving all power in the hands of',
 'parliamentary principle of vesting legislative power in the decision of',
 'level of a real governing power to that of a',
 'government uses the instruments of power in its hands for']

In [49]:
textList_mk = []
filtered_sentences = extract_sentences_with_word(hitler, input_word)
for sentence in filtered_sentences:
    textList_mk.append(sentence)
print(textList_mk)
print(len(textList_mk))

['especially in dark days of distress, such men have the power of healing broken hearts and of raising the despairing spirit of a people.', 'these powers are great britain and italy.', 'should some practical problem suddenly demand examination or solution, memory will immediately select the requisite information from the mass that has been acquired through years of reading and will place this information at the service of a man’s powers of judgment so he may gain a new and clearer view of the problem, or even solve it.', 'god knows, we germans have never been lacking in abundant scientific culture, but we have always had a considerable lack of will-power and of the capacity for making decisions.', 'all the material inventions which we see around us have been produced by the creative powers and capabilities of individuals, and all these inventions help man to raise himself higher and higher above the animal world and to separate himself from that world in an absolutely definite way.', '

#### Trump

In [50]:
text_trump = Text(word_list_trump)

textList_trump = Text(text_trump)
textList_trump.concordance(input_word, width=100, lines=5)
textList_trump = textList_trump.concordance_list(input_word, width=22, lines=1000)
textList_trump = [' '.join(line.left) + ' ' + input_word + ' ' + ' '.join(line.right) for line in textList_trump]
textList_trump[:10]

Displaying 5 of 123 matches:
chigan. Tomorrow, you have the power, with the power of your vote, but you have a power to save Ame
r, with the power of your vote, but you have a power to save America, for this country will never b
 we’re going to win tomorrow. We are returning power to you, the American people. With your help, y
ere treated very rough. Tomorrow, you have the power to do so much for our country. You have the po
er to do so much for our country. You have the power to vote. So go out and vote. Unless you’re goi


['have the power, with the power of your vote, but',
 'vote, but you have a power to save America, for',
 'win tomorrow. We are returning power to you, the American',
 'rough. Tomorrow, you have the power to do so much',
 'our country. You have the power to vote. So go',
 'they say, “You have the power to vote and it',
 'our country. We are returning power to you, the American',
 'America into the manufacturing super power of the world, and',
 'the vote. You have the power really, to save America.',
 'our country. We are returning power to you, the American']

In [51]:
textList_trump = []
filtered_sentences = extract_sentences_with_word(trump, input_word)
for sentence in filtered_sentences:
    textList_trump.append(sentence)
print(textList_trump)

['of course, you want to return the power, especially when it comes to schools.', 'i said in a speech recently, somebody said, “what do you think xi?” i said, “he’s a very powerful strong man.', 'in the wings, they’ve got a local racist democrat district attorney in atlanta who is doing everything in her power to indict me over an absolutely perfect phone call, even more perfect than the one i made with the president of ukraine.', 'now the trucks probably don’t have the power.', 'our opponents have proven many times again and again, that they will say, and do anything to get back into power.', 'my focus now turns to ensuring a smooth, orderly and seamless transition of power.', 'i think it is the power and maybe the money.', 'and we have other things to possibly get ready for, because the bigger ballgame, we have to be respected as a military power, because if we’re not respected, these other countries that are very big, very powerful countries, they will take advantage of us, and you 

#### Biden

In [52]:
text_biden = Text(word_list_biden)

textList_biden = Text(text_biden)
textList_biden.concordance(input_word, width=100, lines=5)
textList_biden = textList_biden.concordance_list(input_word, width=22, lines=1000)
textList_biden = [' '.join(line.left) + ' ' + input_word + ' ' + ' '.join(line.right) for line in textList_biden]
textList_biden[:10]

Displaying 5 of 119 matches:
e’ve got a million people in Louisiana without power and for a time Ida caused the Mississippi Rive
ads that are impassable due to debris and down power lines. And we need people to continue to shelt
e the amount of time it’s going to take to get power back up for everyone in the region. And we’ve 
n moments like these, we can certainly see the power of government to respond to the needs of the p
n IBW electrical worker who climbs up in those power lines in the middle of the storm to try to put


['million people in Louisiana without power and for a time',
 'due to debris and down power lines. And we need',
 'going to take to get power back up for everyone',
 'we can certainly see the power of government to respond',
 'who climbs up in those power lines in the middle',
 'region with significant flooding and power outages that could affect',
 'in place to address significant power outages and resources and',
 'radios, in case of extended power outages. And don’t forget,',
 'heard me say, with the power of our example, not',
 'rights don’t flow from the power of the government. These']

In [53]:
textList_biden = []
filtered_sentences = extract_sentences_with_word(biden, input_word)
for sentence in filtered_sentences:
    textList_biden.append(sentence)
print(textList_biden)

['i will do everything in my power to limit the pain the american people are feeling the gas pump.', 'we’ll demonstrate to the world, the united states is not only back at the table but hopefully leading by the power of our example.', 'demonstrating that our commitment human rights begins at home is among the most powerful and persuasive tools in our foreign policy kit.', 'the thing they most need are power, water, communication systems to get back to some sense of being able to communicate with one another as rapidly as they possibly can.', 'make sure you have the supplies for your entire household, including necessary medications, and food, water, battery powered radios, in case of extended power outages.', 'and as the united states seeks to rally the world action, we will lead not just through the example of our power, but god willing with the power of our example.', 'these are conventionally-armed submarines that are powered by nuclear reactors.', 'you know, we need more stronger l

#### Bush

In [54]:
text_bush = Text(word_list_bush)

textList_bush = Text(text_bush)
textList_bush.concordance(input_word, width=100, lines=5)
textList_bush = textList_bush.concordance_list(input_word, width=22, lines=1000)
textList_bush = [' '.join(line.left) + ' ' + input_word + ' ' + ' '.join(line.right) for line in textList_bush]
textList_bush[:10]

Displaying 5 of 77 matches:
 this new era, our challenge is to harness the power of science to ease human suffering without san
 are clear to me: Removing Saddam Hussein from power was the right decision, and this is a fight Am
age in our strong belief in the transformative power of liberty. So we're helping the people of Ira
free Iraq will be an example for others of the power of liberty to change the societies and to disp
f all people, should never be surprised by the power of our ideals. Eventually, the call of freedom


['challenge is to harness the power of science to ease',
 'me: Removing Saddam Hussein from power was the right decision,',
 "strong belief in the transformative power of liberty. So we're",
 'example for others of the power of liberty to change',
 'never be surprised by the power of our ideals. Eventually,',
 'now without a throne. His power to harm a single',
 "continue to have the coward's power to plant roadside bombs",
 'to do everything in my power to keep us safe.',
 'will do all in their power to spread violence and',
 'not carried forward by our power alone. We can trust']

In [55]:
textList_bush = []
filtered_sentences = extract_sentences_with_word(bush, input_word)
for sentence in filtered_sentences:
    textList_bush.append(sentence)
print(textList_bush)

['we exercise power without conquest, and we sacrifice for the liberty of strangers.', 'we owe it to all our citizens to do everything in our power to prevent that day from coming.', 'we will preserve the peace by building good relations among the great powers.', 'with a new national commitment, our scientists and engineers will overcome obstacles to taking these cars from laboratory to showroom, so that the first car driven by a child born today could be powered by hydrogen and pollution-free.', 'i know this is in our reach because we are guided by a power larger than ourselves who creates us equal in his image.', 'successful societies limit the power of the state and the power of the military -- so that governments respond to the will of the people, and not the will of an elite.', 'as democracy takes hold in iraq, the enemies of freedom will do all in their power to spread violence and fear.', 'that power brought settlers on perilous journeys, inspired colonies to rebellion, ended th

#### Obama

In [56]:
text_obama = Text(word_list_obama)
textList_obama = Text(text_obama)
textList_obama.concordance(input_word, width=100, lines=5)
textList_obama = textList_obama.concordance_list(input_word, width=1000, lines=1000)
#textList_obama = [' '.join(line.left) + ' ' + input_word + ' ' + ' '.join(line.right) for line in textList_obama]
#textList_obama[:10]

Displaying 5 of 112 matches:
ies to protect the planet while unleashing the power of clean energy to serve as an engine of growt
. But that depends upon economies that tap the power of our people, including the potential of wome
d in the democratic process. He focuses on the power of ordinary Americans to bring about change. H
 It was on these streets where I witnessed the power of faith and the quiet dignity of working peop
: No, no, no, no, no, the peaceful transfer of power from one freely elected President to the next.


In [57]:
textList_obama = []
filtered_sentences = extract_sentences_with_word(obama, input_word)
for sentence in filtered_sentences:
    textList_obama.append(sentence)
print(textList_obama)

['our prosperity provides a foundation for our power.', 'we believe the little girl who’s offered an escape from poverty by a great teacher or a grant for college could become the next steve jobs or the scientist who cures cancer or the president of the united states, and it is in our power to give her that chance.', 'the message would have been clear:\xa0 keep power by killing as many people as it takes.', 'we can further empower the forces of rejectionism and hate.', 'in all that we do, we must remember that what sets america apart is not solely our power -– it is the principles upon which our union was founded.', 'or will we lead wisely, using all elements of our power to defeat new threats and protect our planet?', 'to african americans, the story of the exodus was perhaps the central story, the most powerful image about emerging from the grip of bondage to reach for liberty and human dignity -- a tale that was carried from slavery through the civil rights movement into today.', 'a

----------------

## Kosinus-Ähnlichkeit nach Keyword untersuchen

In [233]:
input_word = input("Bitte Wort eingeben...")

#funktion zur extraktion von sätzen über suchwort
def extract_sentences_with_word(text, input_word):

    #lowercase umwandlung
    text = [sentence.lower() for sentence in text]

    #sätze nach suchwort filtern
    sentences_with_word = {sentence.strip() for sentence in text if input_word in sentence}

    return sentences_with_word

textList_mk = []
filtered_sentences = extract_sentences_with_word(hitler, input_word)
for sentence in filtered_sentences:
    textList_mk.append(sentence)

textList_trump = []
filtered_sentences = extract_sentences_with_word(trump, input_word)
for sentence in filtered_sentences:
    textList_trump.append(sentence)

textList_biden = []
filtered_sentences = extract_sentences_with_word(biden, input_word)
for sentence in filtered_sentences:
    textList_biden.append(sentence)

textList_bush = []
filtered_sentences = extract_sentences_with_word(bush, input_word)
for sentence in filtered_sentences:
    textList_bush.append(sentence)

textList_obama = []
filtered_sentences = extract_sentences_with_word(obama, input_word)
for sentence in filtered_sentences:
    textList_obama.append(sentence)

Bitte Wort eingeben...future


#### Trump

In [234]:
#festgelegtes modell
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')


#eingelesene texte
text1 = textList_mk
text2 = textList_trump

name1 = "Hitler" #name aus text1 eingeben (z.B. textList_mk = Hitler)
name2 = "Trump"

#embeddings berechnen
embeddings1 = model.encode(text1, convert_to_tensor=True)
embeddings2 = model.encode(text2, convert_to_tensor=True)

#faiss-integration
index = faiss.IndexFlatL2(embeddings2.shape[1])  #verwendet l2-distanz (euklidisch)
faiss.normalize_L2(embeddings2.numpy())
index.add(embeddings2.numpy())

#suche für jedes embedding aus text 1 die nächsten nachbarn in Text 2
k = 10  # anzahl der nächsten nachbarn
distances, indices = index.search(embeddings1.numpy(), k)

#funktion zur Berechnung der Manhattan-Distanz
def manhattan_distance(vec1, vec2):
    return np.sum(np.abs(vec1 - vec2))

#funktion zur Berechnung der Minkowski-Distanz
def minkowski_distance(vec1, vec2, p=3):
    return np.sum(np.abs(vec1 - vec2) ** p) ** (1 / p)

#filtert sätze nach threshold
similar_pairs = []
similarity_threshold = 0.3  #threshold-wert für cosine similarity
p_value = 3  #beispiel für den Parameter p der Minkowski-Distanz

for i, (dists, inds) in enumerate(zip(distances, indices)):
    for dist, idx in zip(dists, inds):
        sentence1 = text1[i]
        sentence2 = text2[idx]
        if len(sentence1.split()) >= 4 and len(sentence2.split()) >= 4:
            cosine_sim = util.pytorch_cos_sim(embeddings1[i].unsqueeze(0), embeddings2[idx].unsqueeze(0)).item()
            if cosine_sim > similarity_threshold:
                manhattan_dist = manhattan_distance(embeddings1[i].numpy(), embeddings2[idx].numpy())
                minkowski_dist = minkowski_distance(embeddings1[i].numpy(), embeddings2[idx].numpy(), p=p_value)
                similar_pairs.append((sentence1, sentence2, f"{name1} - Satz{i+1}", f"{name2} - Satz{idx+1}", dist, cosine_sim, manhattan_dist, minkowski_dist))

#ausgabe sortiert nach höchster cosine similarity (über reverse=True)
similar_pairs.sort(key=lambda x: x[5], reverse=True)

#ausgabe nach cosine sim und euklidischer distanz
print("Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):")
for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
    print(f"{source1}: \"{sentence1}\" \n{source2}: \"{sentence2}\"")
    print(f"***Cosine-Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n")


#ausgabe der ähnlichen paare in eine textdatei schreiben
#input_name = input("Bitte Biden/Trump/Hitler/Bush eingeben...").lower()
output_file = "similar_pairs_" + input_word + "_" + name2.lower() + ".txt"
folder_path = os.path.join("similar_pairs", input_word)
os.makedirs(folder_path, exist_ok=True)
output_file = os.path.join(folder_path, output_file)

with open(output_file, "w", encoding="utf-8") as file:
    file.write("Gefilterte Sätze mit Cosine Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine Similarity sortiert):\n\n")
    for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
        file.write(f"{source1}: \"{sentence1}\"\n{source2}: \"{sentence2}\"\n")
        file.write(f"***Cosine Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n\n")

print(f"Die ähnlichen Sätze wurden in die Datei '{output_file}' geschrieben.")


Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):
Hitler - Satz160: "therein lies a lesson for the future." 
Trump - Satz63: "“sir, think to the future."
***Cosine-Similarity: 0.6472, Euklidische Distanz: 22.6666, Manhattan-Distanz: 72.9124, Minkowski-Distanz (p=3): 2.0993***

Hitler - Satz134: "then, of course, the social democratic party will raise a horrified outcry and appeal to the authority of the state, which it has just repudiated and will, in most cases, quietly achieve its aim amid the general confusion, namely, to discover some bovine creature holding an important government position, who, in a vain attempt to curry favour with the dreaded opponent in case of future trouble, is ready to finish off those who dare to oppose this world enemy." 
Trump - Satz15: "the task for our movement and our party is to stand up to this destructive agenda with confidence and with result, the future of the 

#### Biden

In [235]:
#festgelegtes modell
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')


#eingelesene texte
text1 = textList_mk
text2 = textList_biden

name1 = "Hitler" #name aus text1 eingeben (z.B. textList_mk = Hitler)
name2 = "Biden"

#embeddings berechnen
embeddings1 = model.encode(text1, convert_to_tensor=True)
embeddings2 = model.encode(text2, convert_to_tensor=True)

#faiss-integration
index = faiss.IndexFlatL2(embeddings2.shape[1])  #verwendet l2-distanz (euklidisch)
faiss.normalize_L2(embeddings2.numpy())
index.add(embeddings2.numpy())

#suche für jedes embedding aus text 1 die nächsten nachbarn in Text 2
k = 10  # anzahl der nächsten nachbarn
distances, indices = index.search(embeddings1.numpy(), k)

#funktion zur Berechnung der Manhattan-Distanz
def manhattan_distance(vec1, vec2):
    return np.sum(np.abs(vec1 - vec2))

#funktion zur Berechnung der Minkowski-Distanz
def minkowski_distance(vec1, vec2, p=3):
    return np.sum(np.abs(vec1 - vec2) ** p) ** (1 / p)

#filtert sätze nach threshold
similar_pairs = []
similarity_threshold = 0.3  #threshold-wert für cosine similarity
p_value = 3  #beispiel für den Parameter p der Minkowski-Distanz

for i, (dists, inds) in enumerate(zip(distances, indices)):
    for dist, idx in zip(dists, inds):
        sentence1 = text1[i]
        sentence2 = text2[idx]
        if len(sentence1.split()) >= 4 and len(sentence2.split()) >= 4:
            cosine_sim = util.pytorch_cos_sim(embeddings1[i].unsqueeze(0), embeddings2[idx].unsqueeze(0)).item()
            if cosine_sim > similarity_threshold:
                manhattan_dist = manhattan_distance(embeddings1[i].numpy(), embeddings2[idx].numpy())
                minkowski_dist = minkowski_distance(embeddings1[i].numpy(), embeddings2[idx].numpy(), p=p_value)
                similar_pairs.append((sentence1, sentence2, f"{name1} - Satz{i+1}", f"{name2} - Satz{idx+1}", dist, cosine_sim, manhattan_dist, minkowski_dist))

#ausgabe sortiert nach höchster cosine similarity (über reverse=True)
similar_pairs.sort(key=lambda x: x[5], reverse=True)

#ausgabe nach cosine sim und euklidischer distanz
print("Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):")
for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
    print(f"{source1}: \"{sentence1}\" \n{source2}: \"{sentence2}\"")
    print(f"***Cosine-Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n")


#ausgabe der ähnlichen paare in eine textdatei schreiben
#input_name = input("Bitte Biden/Trump/Hitler/Bush eingeben...").lower()
output_file = "similar_pairs_" + input_word + "_" + name2.lower() + ".txt"
folder_path = os.path.join("similar_pairs", input_word)
os.makedirs(folder_path, exist_ok=True)
output_file = os.path.join(folder_path, output_file)

with open(output_file, "w", encoding="utf-8") as file:
    file.write("Gefilterte Sätze mit Cosine Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine Similarity sortiert):\n\n")
    for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
        file.write(f"{source1}: \"{sentence1}\"\n{source2}: \"{sentence2}\"\n")
        file.write(f"***Cosine Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n\n")

print(f"Die ähnlichen Sätze wurden in die Datei '{output_file}' geschrieben.")


Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Biden - Satz114: "and the best part is making these ambitious investments isn’t just good climate policy, it’s a chance for each of our countries to invest in ourselves and our own future."
***Cosine-Similarity: 0.4725, Euklidische Distanz: 14.6752, Manhattan-Distanz: 59.2920, Minkowski-Distanz (p=3): 1.6707***

Hitler - Satz17: "successes achieved through coalitions, owing to the very nature of their source carry in them from the very start the germs of future disintegration and the possibility of losing what has already been achieved." 
Biden - Satz61: "we have to build that foundation for the future for success."
***Cosine-Similarity: 0.4724, Euklidische Distanz: 17.0853, Manhattan-Distanz: 64.6749, Minkowski-Distanz (p=3): 1.8216***

Hitler - Satz28: "it can be changed only if, through a spirit of mutual tolerance, the nation can be assured of a future, the greatness of which will gradually operate as a conciliating

#### Bush

In [236]:
#festgelegtes modell
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')


#eingelesene texte
text1 = textList_mk
text2 = textList_bush

name1 = "Hitler" #name aus text1 eingeben (z.B. textList_mk = Hitler)
name2 = "Bush"

#embeddings berechnen
embeddings1 = model.encode(text1, convert_to_tensor=True)
embeddings2 = model.encode(text2, convert_to_tensor=True)

#faiss-integration
index = faiss.IndexFlatL2(embeddings2.shape[1])  #verwendet l2-distanz (euklidisch)
faiss.normalize_L2(embeddings2.numpy())
index.add(embeddings2.numpy())

#suche für jedes embedding aus text 1 die nächsten nachbarn in Text 2
k = 10  # anzahl der nächsten nachbarn
distances, indices = index.search(embeddings1.numpy(), k)

#funktion zur Berechnung der Manhattan-Distanz
def manhattan_distance(vec1, vec2):
    return np.sum(np.abs(vec1 - vec2))

#funktion zur Berechnung der Minkowski-Distanz
def minkowski_distance(vec1, vec2, p=3):
    return np.sum(np.abs(vec1 - vec2) ** p) ** (1 / p)

#filtert sätze nach threshold
similar_pairs = []
similarity_threshold = 0.3  #threshold-wert für cosine similarity
p_value = 3  #beispiel für den Parameter p der Minkowski-Distanz

for i, (dists, inds) in enumerate(zip(distances, indices)):
    for dist, idx in zip(dists, inds):
        sentence1 = text1[i]
        sentence2 = text2[idx]
        if len(sentence1.split()) >= 4 and len(sentence2.split()) >= 4:
            cosine_sim = util.pytorch_cos_sim(embeddings1[i].unsqueeze(0), embeddings2[idx].unsqueeze(0)).item()
            if cosine_sim > similarity_threshold:
                manhattan_dist = manhattan_distance(embeddings1[i].numpy(), embeddings2[idx].numpy())
                minkowski_dist = minkowski_distance(embeddings1[i].numpy(), embeddings2[idx].numpy(), p=p_value)
                similar_pairs.append((sentence1, sentence2, f"{name1} - Satz{i+1}", f"{name2} - Satz{idx+1}", dist, cosine_sim, manhattan_dist, minkowski_dist))

#ausgabe sortiert nach höchster cosine similarity (über reverse=True)
similar_pairs.sort(key=lambda x: x[5], reverse=True)

#ausgabe nach cosine sim und euklidischer distanz
print("Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):")
for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
    print(f"{source1}: \"{sentence1}\" \n{source2}: \"{sentence2}\"")
    print(f"***Cosine-Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n")


#ausgabe der ähnlichen paare in eine textdatei schreiben
#input_name = input("Bitte Biden/Trump/Hitler/Bush eingeben...").lower()
output_file = "similar_pairs_" + input_word + "_" + name2.lower() + ".txt"
folder_path = os.path.join("similar_pairs", input_word)
os.makedirs(folder_path, exist_ok=True)
output_file = os.path.join(folder_path, output_file)

with open(output_file, "w", encoding="utf-8") as file:
    file.write("Gefilterte Sätze mit Cosine Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine Similarity sortiert):\n\n")
    for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
        file.write(f"{source1}: \"{sentence1}\"\n{source2}: \"{sentence2}\"\n")
        file.write(f"***Cosine Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n\n")

print(f"Die ähnlichen Sätze wurden in die Datei '{output_file}' geschrieben.")


Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):
Hitler - Satz160: "therein lies a lesson for the future." 
Bush - Satz37: "but that future will come."
***Cosine-Similarity: 0.6289, Euklidische Distanz: 22.8622, Manhattan-Distanz: 74.4393, Minkowski-Distanz (p=3): 2.0949***

Hitler - Satz70: "we were fighting for the freedom and independence of our country, for the security of our future welfare and the honour of the nation." 
Bush - Satz88: "the freedom of many, and the future security of our nation, now depend on us."
***Cosine-Similarity: 0.6142, Euklidische Distanz: 17.1368, Manhattan-Distanz: 63.3646, Minkowski-Distanz (p=3): 1.8084***

Hitler - Satz148: "what form shall the life of the nation assume in the near future that is to say within such a period as we can forecast?" 
Bush - Satz37: "but that future will come."
***Cosine-Similarity: 0.6087, Euklidische Distanz: 21.6125, Manhattan-Distan

#### Obama

In [237]:
#festgelegtes modell
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')


#eingelesene texte
text1 = textList_mk
text2 = textList_obama

name1 = "Hitler" #name aus text1 eingeben (z.B. textList_mk = Hitler)
name2 = "Obama"

#embeddings berechnen
embeddings1 = model.encode(text1, convert_to_tensor=True)
embeddings2 = model.encode(text2, convert_to_tensor=True)

#faiss-integration
index = faiss.IndexFlatL2(embeddings2.shape[1])  #verwendet l2-distanz (euklidisch)
faiss.normalize_L2(embeddings2.numpy())
index.add(embeddings2.numpy())

#suche für jedes embedding aus text 1 die nächsten nachbarn in Text 2
k = 10  # anzahl der nächsten nachbarn
distances, indices = index.search(embeddings1.numpy(), k)

#funktion zur Berechnung der Manhattan-Distanz
def manhattan_distance(vec1, vec2):
    return np.sum(np.abs(vec1 - vec2))

#funktion zur Berechnung der Minkowski-Distanz
def minkowski_distance(vec1, vec2, p=3):
    return np.sum(np.abs(vec1 - vec2) ** p) ** (1 / p)

#filtert sätze nach threshold
similar_pairs = []
similarity_threshold = 0.3  #threshold-wert für cosine similarity
p_value = 3  #beispiel für den Parameter p der Minkowski-Distanz

for i, (dists, inds) in enumerate(zip(distances, indices)):
    for dist, idx in zip(dists, inds):
        sentence1 = text1[i]
        sentence2 = text2[idx]
        if len(sentence1.split()) >= 4 and len(sentence2.split()) >= 4:
            cosine_sim = util.pytorch_cos_sim(embeddings1[i].unsqueeze(0), embeddings2[idx].unsqueeze(0)).item()
            if cosine_sim > similarity_threshold:
                manhattan_dist = manhattan_distance(embeddings1[i].numpy(), embeddings2[idx].numpy())
                minkowski_dist = minkowski_distance(embeddings1[i].numpy(), embeddings2[idx].numpy(), p=p_value)
                similar_pairs.append((sentence1, sentence2, f"{name1} - Satz{i+1}", f"{name2} - Satz{idx+1}", dist, cosine_sim, manhattan_dist, minkowski_dist))

#ausgabe sortiert nach höchster cosine similarity (über reverse=True)
similar_pairs.sort(key=lambda x: x[5], reverse=True)

#ausgabe nach cosine sim und euklidischer distanz
print("Gefilterte Sätze mit Cosine-Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine-Similarity sortiert):")
for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
    print(f"{source1}: \"{sentence1}\" \n{source2}: \"{sentence2}\"")
    print(f"***Cosine-Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n")


#ausgabe der ähnlichen paare in eine textdatei schreiben
#input_name = input("Bitte Biden/Trump/Hitler/Bush eingeben...").lower()
output_file = "similar_pairs_" + input_word + "_" + name2.lower() + ".txt"
folder_path = os.path.join("similar_pairs", input_word)
os.makedirs(folder_path, exist_ok=True)
output_file = os.path.join(folder_path, output_file)

with open(output_file, "w", encoding="utf-8") as file:
    file.write("Gefilterte Sätze mit Cosine Similarity, euklidischer Distanz, Manhattan-Distanz und Minkowski-Distanz (nach Cosine Similarity sortiert):\n\n")
    for idx, (sentence1, sentence2, source1, source2, euc_distance, cosine_sim, manhattan_dist, minkowski_dist) in enumerate(similar_pairs, start=1):
        file.write(f"{source1}: \"{sentence1}\"\n{source2}: \"{sentence2}\"\n")
        file.write(f"***Cosine Similarity: {cosine_sim:.4f}, Euklidische Distanz: {euc_distance:.4f}, Manhattan-Distanz: {manhattan_dist:.4f}, Minkowski-Distanz (p={p_value}): {minkowski_dist:.4f}***\n\n")

print(f"Die ähnlichen Sätze wurden in die Datei '{output_file}' geschrieben.")


Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Hitler - Satz89: "measures of momentous importance for the future existence of the state are framed and discussed in an atmosphere more suited to the card-table." 
Obama - Satz80: "that's part of a brighter future."
***Cosine-Similarity: 0.4706, Euklidische Distanz: 17.0411, Manhattan-Distanz: 62.9245, Minkowski-Distanz (p=3): 1.8284***

Hitler - Satz96: "even in future we should be doomed to remain mere manure for civilisation, and that not in the banal sense of the contemporary bourgeois mind, which sees in a lost fellow-member of our people only a lost citizen, but in a sense which we should have to recognise in sorrow, namely, that our, racial blood would be destined to disappear." 
Obama - Satz131: "like generations have before us, we must reject that future."
***Cosine-Similarity: 0.4705, Euklidische Distanz: 15.7641, Manhattan-Distanz: 61.3244, Minkowski-Distanz (p=3): 1.7256***

Hitler - Satz76: "the temporary p